# Table of Contents
 <p><div class="lev1 toc-item"><a href="#Ground-predictions" data-toc-modified-id="Ground-predictions-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Ground predictions</a></div><div class="lev2 toc-item"><a href="#PVLib-Clearsky" data-toc-modified-id="PVLib-Clearsky-11"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>PVLib Clearsky</a></div>

In [1]:
import pandas as pd
import numpy as np
import os
import datetime
import matplotlib
import matplotlib.pyplot as plt
from mpl_toolkits.axes_grid1 import make_axes_locatable
from sklearn import tree

import pytz
import itertools
import visualize
import utils
import pydotplus

from sklearn import metrics

import pvlib
import cs_detection
# import visualize
# from bokeh.plotting import output_notebook
# output_notebook()

import visualize_plotly as visualize

from IPython.display import Image

%load_ext autoreload
%autoreload 2

np.set_printoptions(precision=4)
%matplotlib notebook

# Ground predictions

## PVLib Clearsky

Only making ground predictions using PVLib clearsky model and statistical model.  NSRDB model won't be available to ground measurements.

In [2]:
nsrdb = cs_detection.ClearskyDetection.read_pickle('ornl_nsrdb_1.pkl.gz')
nsrdb.df.index = nsrdb.df.index.tz_convert('EST')

In [3]:
nsrdb.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [4]:
ground = cs_detection.ClearskyDetection.read_pickle('ornl_ground_1.pkl.gz')
ground.df.index = ground.df.index.tz_convert('EST')

We will reduce the frequency of ground based measurements to match NSRDB.

In [5]:
ground.intersection(nsrdb.df.index)

In [6]:
nsrdb.scale_model('GHI', 'Clearsky GHI pvlib', 'sky_status')

In [7]:
nsrdb.calc_all_window_metrics(3, 30, col1='GHI', col2='Clearsky GHI pvlib', overwrite=True)

In [8]:
ground.calc_all_window_metrics(3, 30, col1='GHI', col2='Clearsky GHI pvlib', overwrite=True)

In [9]:
feature_cols = [
'GHI',
'Clearsky GHI pvlib',
'tfn',
'GHI mean',
'GHI std',
'GHI max',
'GHI min',
'GHI range',
'Clearsky GHI pvlib mean',
'Clearsky GHI pvlib std',
'Clearsky GHI pvlib max',
'Clearsky GHI pvlib min',
'Clearsky GHI pvlib range',
'GHI gradient',
'GHI gradient mean',
'GHI gradient std',
'GHI gradient max',
'GHI gradient min',
'GHI gradient range',
'GHI gradient second',
'GHI gradient second mean',
'GHI gradient second std',
'GHI gradient second max',
'GHI gradient second min',
'GHI gradient second range',
'Clearsky GHI pvlib gradient',
'Clearsky GHI pvlib gradient mean',
'Clearsky GHI pvlib gradient std',
'Clearsky GHI pvlib gradient max',
'Clearsky GHI pvlib gradient min',
'Clearsky GHI pvlib gradient second',
'Clearsky GHI pvlib gradient second mean',
'Clearsky GHI pvlib gradient second std',
'Clearsky GHI pvlib gradient second max',
'Clearsky GHI pvlib gradient second min',
'abs_ideal_ratio_diff',
'abs_ideal_ratio_diff mean',
'abs_ideal_ratio_diff std',
'abs_ideal_ratio_diff max',
'abs_ideal_ratio_diff min',
'abs_ideal_ratio_diff range',
'abs_ideal_ratio_diff gradient',
'abs_ideal_ratio_diff gradient mean',
'abs_ideal_ratio_diff gradient std',
'abs_ideal_ratio_diff gradient max',
'abs_ideal_ratio_diff gradient min',
'abs_ideal_ratio_diff gradient range',
'abs_ideal_ratio_diff gradient second',
'abs_ideal_ratio_diff gradient second mean',
'abs_ideal_ratio_diff gradient second std',
'abs_ideal_ratio_diff gradient second max',
'abs_ideal_ratio_diff gradient second min',
'abs_ideal_ratio_diff gradient second range',
'abs_diff',
'abs_diff mean',
'abs_diff std',
'abs_diff max',
'abs_diff min',
'abs_diff range',
'abs_diff gradient',
'abs_diff gradient mean',
'abs_diff gradient std',
'abs_diff gradient max',
'abs_diff gradient min',
'abs_diff gradient range',
'abs_diff gradient second',
'abs_diff gradient second mean',
'abs_diff gradient second std',
'abs_diff gradient second max',
'abs_diff gradient second min',
'abs_diff gradient second range',
'GHI line length',
'Clearsky GHI pvlib line length',
'GHI Clearsky GHI pvlib line length ratio']

target_cols = ['sky_status']

In [10]:
ground.trim_dates('10-01-2009', '10-15-2009')

In [11]:
ground.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [12]:
train = cs_detection.ClearskyDetection(nsrdb.df)
test = cs_detection.ClearskyDetection(ground.df)

In [13]:
from sklearn import ensemble
# clf = ensemble.RandomForestClassifier(class_weight='balanced', n_estimators=100, max_leaf_nodes=40)  # max_leaf_nodes=30, n_estimators=100)
clf = tree.DecisionTreeClassifier(class_weight='balanced', min_samples_leaf=.005)
# clf = ensemble.RandomForestClassifier(class_weight='balanced', min_samples_leaf=.0025, n_estimators=100)

# clf = ensemble.RandomForestClassifier(class_weight='balanced', min_samples_leaf=.05, n_estimators=100)
# clf = tree.DecisionTreeClassifier(class_weight='balanced', min_samples_leaf=.005, max_depth=10)


In [14]:
# nsrdb.df = nsrdb.df[nsrdb.df['GHI'] > 0]

In [15]:
# train.df = train.df[train.df['Clearsky GHI pvlib'] > 0]

In [16]:
clf.fit(train.df[feature_cols].values, train.df[target_cols].values.flatten())

DecisionTreeClassifier(class_weight='balanced', criterion='gini',
            max_depth=None, max_features=None, max_leaf_nodes=None,
            min_impurity_split=1e-07, min_samples_leaf=0.005,
            min_samples_split=2, min_weight_fraction_leaf=0.0,
            presort=False, random_state=None, splitter='best')

In [17]:
# pred = clf.predict(test.df[feature_cols].values)
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 3)
pred = pred.astype(bool)

1 1
2 1.00966679749
3 1.00060906974
4 1.00000001481
5 1.0
1 1
2 1.02639528048
3 1.0
1 1
2 1.01081513554
3 1.0
1 1
2 0.843264452855
3 0.907202914855
4 0.918776295793
5 0.97876032508
6 0.952432337255
7 1.0
1 1
2 2.61803396034
1 1
2 2.61803396034
1 1
2 1.02252151893
3 1.0
1 1
2 0.983470912932
3 1.0
1 1
2 1.00538672325
3 1.0
1 1
2 2.61803396034
1 1
2 0.961263037919
3 1.0
1 1
2 2.61803396034
1 1
2 2.61803396034
1 1
2 2.61803396034


In [18]:
train.intersection(test.df.index)

In [19]:
cm = metrics.confusion_matrix(train.df['sky_status'].values, pred)
vis = visualize.Visualizer()
vis.plot_confusion_matrix(cm, labels=['cloudy', 'clear'])

In [20]:
metrics.f1_score(train.df['sky_status'].values, pred)

0.72368421052631582

In [21]:
vis = visualize.Visualizer()

In [22]:
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[(train.df['sky_status'] == 0) & (pred)]['GHI'], 'ML clear only')
vis.add_circle_ser(test.df[(train.df['sky_status'] == 1) & (~pred)]['GHI'], 'NSRDB clear only')
vis.add_circle_ser(test.df[(train.df['sky_status'] == 1) & (pred)]['GHI'], 'ML+NSRDB clear only')

In [23]:
vis.show()

In [24]:
ground = cs_detection.ClearskyDetection.read_pickle('ornl_ground_1.pkl.gz')

In [25]:
ground.df.index = ground.df.index.tz_convert('EST')

In [26]:
ground.trim_dates('11-01-2009', '11-15-2009')

In [27]:
ground.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [28]:
test = ground

In [29]:
# pred = clf.predict(test.df[feature_cols].values)
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 10, smooth=True)
pred = pred.astype(bool)

1 1
2 1.01828040266
3 0.999974144461
4 1.0
1 1
2 1.00398585008
3 1.00006204046
4 1.0
1 1
2 0.986616055973
3 1.00004332596
4 1.0
1 1
2 0.994482315976
3 0.99998352293
4 1.0
1 1
2 1.01883705523
3 1.00012199248
4 1.0
1 1
2 1.00680229176
3 1.00002043201
4 1.0
1 1
2 1.00066283711
3 1.00000316084
4 1.0
1 1
2 1.00691183409
3 1.00127300284
4 1.00003609535
5 1.0
1 1
2 1.00191209171
3 1.0
1 1
2 2.61803396034
1 1
2 0.970088996679
3 0.990850826322
4 0.995103368978
5 1.0
1 1
2 1.00344847348
3 1.00007506984
4 1.0
1 1
2 1.00129320568
3 1.00063886211
4 1.00061686561
5 1.00005431317
6 1.00042811905
7 1.0
1 1
2 1.00721356825
3 1.00109328987
4 1.00013592953
5 1.0


In [30]:
vis = visualize.Visualizer()

In [31]:
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[(test.df['sky_status pvlib'] == 0) & (pred)]['GHI'], 'ML clear only')
vis.add_circle_ser(test.df[(test.df['sky_status pvlib'] == 1) & (~pred)]['GHI'], 'PVLib clear only')
vis.add_circle_ser(test.df[(test.df['sky_status pvlib'] == 1) & (pred)]['GHI'], 'ML+PVLib clear only')

In [32]:
vis.show()

In [33]:
tree.export_graphviz(clf, 'ornl3.dot', feature_names=feature_cols, class_names=['cloudy', 'clear'], filled=True)